# Time Series Project

https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/

![](id_for_ideas/logo.png)

https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/

## 2.2 Etapas en el desarrollo de código



Acá se va exponiendo de forma interactiva las etapas técnicas del desarrollo de código 

# 2.2.1 DATA FEED:  Descripción del acondicionamiento del dataset original

In [1]:
import numpy as np
import pandas as pd
from paquete_proyecto.herramientas.data_info import data_info
import warnings

warnings.filterwarnings("ignore")

In [2]:
from paquete_proyecto.data_feed.bases import importar_databases, ajustes_finales

ventas, ventas_sin_duplicados = importar_databases()

data = ajustes_finales(ventas_sin_duplicados)

## CIERRE ETAPA: 2.2.1 DATA PREPARE

### DATASET: 

#### DESCRIPCION:

- dataset original: con la variable "Fecha" como indice

In [3]:
display(data.sample(3))
display(data_info(data=data, name="ventas"))

IdCliente          NombreCliente  Empleado     Referencia  \
Fecha                                                                    
2018-10-17  C890930545           MINCIVIL S A         3       REC-0171   
2018-07-31   C20982916   VILLAREAL MARIA INES        48  SE-CS-11-0002   
2020-03-02   C79554609  RAMIREZ INFANTE YORFI        14  SE-CS-12-0008   

                       Descripcion  CodigoFamilia     Familia  Cantidad  \
Fecha                                                                     
2018-10-17   REENC XDE2 295/80R225            102  REENCAUCHE         2   
2018-07-31  RECTIFICACION RIN LUJO            106   SERVICIOS         2   
2020-03-02     CAMBIO DE PASTILLAS            106   SERVICIOS         1   

               Ventas Localidad             Sede  Area  
Fecha                                                   
2018-10-17  1166701.0  Engativa  Ventas externas    22  
2018-07-31     5042.0   Usaquen        Santa ana    33  
2020-03-02     2521.0      Suba             Suba    32

info de ventas        columna     type   count  NaN NaN_pct  unique unique_pct
0                   IdCliente   object  108794    0   0.0 %   24087    22.14 %
1               NombreCliente   object  108794    0   0.0 %   21816    20.05 %
2                    Empleado    int32  108794    0   0.0 %      56     0.05 %
3                  Referencia   object  108794    0   0.0 %    1854      1.7 %
4                 Descripcion   object  108794    0   0.0 %    1814     1.67 %
5               CodigoFamilia    int32  108794    0   0.0 %       5      0.0 %
6                     Familia   object  108794    0   0.0 %       5      0.0 %
7                    Cantidad    int32  108794    0   0.0 %     212     0.19 %
8                      Ventas  float64  108794    0   0.0 %   14279    13.12 %
9                   Localidad   object  108794    0   0.0 %       6     0.01 %
10                       Sede   object  108794    0   0.0 %       7     0.01 %
11                       Area    int32  108794    0   0.0 %       7     0.01 %

<div>
    <h4>Definición de las variables del dataset</h4>
    <ol>
        <li> <b>IdCliente</b>: Código identificador de cliente</li>
        <li> <b>NombreCliente</b>: Nombre de cliente, puede ser persona física o jurídica</li>
        <li> <b>Empleado</b>: Código identificado de empleado</li>
        <li> <b>Referencia</b>: Código identificador del producto o servicio</li>
        <li> <b>Descripcion</b>: Información adicional sobre la transacción</li>
        <li> <b>CodigoFamilia</b>: Código identificador de familia</li>
        <li> <b>Familia</b>: Categoría - Rubro o área comercial</li>
        <li> <b>Cantidad</b>: Unidades vendidas en dicha transacción</li>
        <li> <b>Ventas</b>: Monto o volumen de la transacción (expresada en COP)</li>
        <li> <b>Localidad</b>: Región geográfica de la Sede</li>
        <li> <b>Sede</b>: Referencia de la sucursal</li>
        <li> <b>Area</b>: Código identificador de Sede</li>
    </ol>
</div>

-----

# 2.2.2 DATA PREPARE: Tratamiento del dataset de trabajo

<b>1ro)  AÑADIR "Id"</b>

<b>2do) AJUSTE DE TIPO DE CAMBIO: "Ventas_USD"</b>

<b>3ro) CATEGORIZACION</b>

<b>4to) COMPLETAR EL DATASET CON LAS FECHAS FALTANTES</b>
    

## 1ro- AÑADIR "Id"

Añadimos un registro único para cada transacción

In [4]:
from paquete_proyecto.data_prepare.hard_code import hard_category_id

data = hard_category_id(data)

## 2do- AJUSTE DE TIPO DE CAMBIO: "Ventas_USD"

1ro) Se hace un llamado a la API de Alpha Vantage para solicitar la cotización semanal del par COP/USD<br />
2do) Se selecciona el rango de fechas pertencientes al dataset original (255 semanas)<br />
3ro) Se añade la columna "Cotizacion_USD" al dataset<br />
4to) Se añade la columna "Ventas_USD" que refleja el valor de la transacción en dolares.<br />


In [5]:
import os
from dotenv import load_dotenv

load_dotenv()

from paquete_proyecto.data_prepare.forex_api import alpha_vantage_fx_api
from paquete_proyecto.data_prepare.cotizacion import (
    criterio_valor_apertura,
    preparar_cotizacion,
    agregar_cotizacion,
)

In [6]:
TOKEN = os.environ["TOKEN_AV"]

cotizacion = alpha_vantage_fx_api("FX_WEEKLY", "COP", "USD", TOKEN)
cotizacion = criterio_valor_apertura(preparar_cotizacion(data, cotizacion), "COP/USD")

data = agregar_cotizacion(
    data, cotizacion
)  # TODO agregar el parámetro "Cotizacion_USD" (para que quede explicito)
data.loc[:, "Ventas_USD"] = data["Ventas"] * data["Cotizacion_USD"]

## 3ro- CATEGORIZACION

<b>1ro) Variable "Familia": Se añade columna "category_1": Categorizacion binaria "producto", "servicio"</b><br />
    - producto: [LLANTA, FILTRO, LUBRICANTES]
    - servicio: [SERVICIOS, REENCAUCHE]


<b>2do) Categoría "Familia-SERVICIOS": Se añade columna "category_2" que sub-categoriza mediante RegEx a categoría "Familia-SERVICIOS":</b><br />
        - Son 14 etiquetas que surgen por extraccion de patrones RegEx desde la variable "Descripcion"<br />
        - El remamente se categorizó con la etiqueta "otros"

In [7]:
from paquete_proyecto.data_prepare.hard_code import hard_category_1

# CATEGORY_1
data = hard_category_1(data, "category1")

In [8]:
from paquete_proyecto.data_prepare.regex import (
    return_match_id,
    category_apply,
    merge_category,
)

# CATEGORY_2
data_regex_servicios = data.loc[data["Familia"] == "SERVICIOS"].set_index("Id")


patrones = dict(
    balanceo="(BALANCEO)",
    alineacion="(ALINEACION)",
    reparacion="(REPARACION)",
    cambio_de_aceite="(CAMBIO(.?.?.?.?)ACEITE)",
    calibracion="(CALIBRACION)",
    montaje="(MONTAJE)",
    rotacion="(ROTACION)",
    mano_de_obra="(MANO(.?.?.?.?)OBRA)",
    frenos="(AJUSTE(.?.?.?.?)FRENOS|CAMBIO(.?.?.?.?)PASTILLAS|REVISION(.?.?.?.?)FRENOS)",
    rectificacion="(RECTIFICACION)",
    servicios="(SERVICIO(.?))",
    cupon_combo="(CUPON|COMBO)",
    desvare_ruta="(DESVARE(.?.?.?.?.?.?.?.?)RUTA)",
    llanta="((REGRABACION|REMANENTE|INSPECCION|MARCACION|VULCANIZADO)(.?.?.?.?.?.?.?.?.?.?.?.?.?.?.?.?)LLANTA(.?))",
    otros="Patron nulo",
)


indice_categorias = return_match_id(data_regex_servicios, "Descripcion", patrones)
feature_categoria = category_apply(data_regex_servicios, indice_categorias)

data = merge_category(data, feature_categoria, "Id", "category2")

In [9]:
# TODO: Agregar la categoría binaria "camion"
# TODO: dividir la Familia FILTROS en "aceite" y "aire"

## 4to- Completar Fecha Faltantes

In [10]:
from paquete_proyecto.data_prepare.muestreo import complete_dates

data = complete_dates(data)

## CIERRE ETAPA: 2.2.2 DATA PREPARE

### DATASET:

- Se añade "Cotizacion_USD", "Ventas_USD"," category_1", y "category_2"
- Se completan las fechas faltantes

In [11]:
display(data.sample(3))
display(data_info(data=data, name="ventas"))

Id   IdCliente                NombreCliente  Empleado  \
Fecha                                                                   
2020-09-01  108188  C900680675  FRANQUICIAS DIRECT TV S A S        44   
2018-10-08   64273   C80383298          VARGAS LUIS ERNESTO        36   
2018-08-06   59181  C800166199                    DELTEC SA        10   

              Referencia                   Descripcion  CodigoFamilia  \
Fecha                                                                   
2020-09-01  SE-CS-1-0003  ALINEACION CAMION O CABEZOTE            106   
2018-10-08  SE-CS-2-0003               BALANCEO CAMION            106   
2018-08-06      VFR-0368      FILTRO DE ACEITE OLP-122            109   

              Familia  Cantidad  Ventas Localidad      Sede  Area  \
Fecha                                                               
2020-09-01  SERVICIOS         1   42017  Engativa  Calle 80    31   
2018-10-08  SERVICIOS         2   25211  Engativa  Calle 80    31   
2018-08-06    FILTROS         1   62185  Engativa  Calle 80    31   

            Cotizacion_USD  Ventas_USD category1   category2  
Fecha                                                         
2020-09-01         0.00027    11.34459  servicio  alineacion  
2018-10-08         0.00033     8.31963  servicio    balanceo  
2018-08-06         0.00035    21.76475  producto         NaL

info de ventas         columna     type   count  NaN NaN_pct  unique  \
0                           Id    int32  109518    0   0.0 %  108795   
1                    IdCliente   object  109518    0   0.0 %   24088   
2                NombreCliente   object  109518    0   0.0 %   21816   
3                     Empleado    int32  109518    0   0.0 %      57   
4                   Referencia   object  109518    0   0.0 %    1855   
5                  Descripcion   object  109518    0   0.0 %    1815   
6                CodigoFamilia    int32  109518    0   0.0 %       6   
7                      Familia   object  109518    0   0.0 %       6   
8                     Cantidad    int32  109518    0   0.0 %     213   
9                       Ventas    int32  109518    0   0.0 %   14280   
10                   Localidad   object  109518    0   0.0 %       7   
11                        Sede   object  109518    0   0.0 %       8   
12                        Area    int32  109518    0   0.0 %       8   
13              Cotizacion_USD  float64  109518    0   0.0 %      14   
14                  Ventas_USD  float64  109518    0   0.0 %   23553   
15                   category1   object  109518    0   0.0 %       3   
16                   category2   object  109518    0   0.0 %      17   

info de ventas unique_pct  
0                 99.34 %  
1                 21.99 %  
2                 19.92 %  
3                  0.05 %  
4                  1.69 %  
5                  1.66 %  
6                  0.01 %  
7                  0.01 %  
8                  0.19 %  
9                 13.04 %  
10                 0.01 %  
11                 0.01 %  
12                 0.01 %  
13                 0.01 %  
14                21.51 %  
15                  0.0 %  
16                 0.02 %

-----

# (III) RESEARCH: (DESACTUALIZADO)
    1- INDICADORES CON TRATAMIENTO NUMÉRICO

    2- INDICADORES CON TRATAMIENTO CATEGÓRICO


## 1 INDICADORES TRATADOS NUMERICAMENTE

In [12]:
from paquete_proyecto.data_research.numerical import TimeSerieTarget

# Target 1
d1 = TimeSerieTarget(target=data["Ventas_USD"])

# Target 2
d2 = TimeSerieTarget(target=data["Cantidad"])

## 2 INDICADORES TRATADOS CATEGORICAMENTE

In [13]:
from paquete_proyecto.data_research.categorical import TimeSerieBuilder

# INDICADORES TRATATOS CATEGORICAMENTE
features = ["Empleado", "Familia", "Localidad", "Sede", "category1", "category2"]


features_iter = iter(features)

# VOLUMEN DE VENTAS POR CATEGORIA FROM 2016 TO 2021
d3 = TimeSerieBuilder(
    dataset=data[features],
    target=data["Ventas_USD"],
)
d3.transform(lambda x: x.groupby(x.index).sum())
d3.accumulate()

# VOLUMEN DE VENTAS POR CATEGORIA FROM 2019 TO 2021
d4 = TimeSerieBuilder(
    dataset=data[features].loc["2019":],
    target=data["Ventas_USD"].loc["2019":],
)
d4.transform(lambda x: x.groupby(x.index).sum())
d4.accumulate()

# (IV) REPORT:

indicadores solcitados:

1) Venta Total<br />
4) Cantidad de Elementos vendidos<br />

2) Ventas totales por Sedes en cada Rubro o Familia y Servicios (iter_sum)<br />
5) Cantidad de Servicios Ofrecidos (iter_count)<br />


3) Ganancia Facturación Total de Servicios<br />
6) Ventas realizadas por sus empleados<br />
7) Cantidad de Sedes o ubicaciones disponibles<br />
8) Ranking de Ventas / Servicios de Empleados<br />

In [14]:
from paquete_proyecto.data_report.plots import VisualProcessor, BackendPlotter, PlotterStorage, GraphUploader
from paquete_proyecto.data_report.tools import descargar_objeto
from paquete_proyecto.data_report.hard_code import plot_and_storage

In [15]:
## INTRODUCCION A LA EMPRESA SLIDE 1

frame_ventas = d1.targets["accum_Ventas_USD"].to_frame()
frame_cantidad = d2.targets["Cantidad"].to_frame()
frame_ventas_cantidad = d1.targets["Ventas_USD"].to_frame()


dataframe_list_1 = [frame_ventas, frame_cantidad]
dataframe_list_2 = [frame_ventas.loc["2019":], frame_cantidad.loc["2019":]]
dataframe_list_3 = [frame_ventas_cantidad.loc["2019":]]


visual_1 = VisualProcessor(frame_list=dataframe_list_1, features=["accum_Ventas_USD", "Cantidad"])
visual_1_1 = VisualProcessor(frame_list=dataframe_list_2, features=["accum_Ventas_USD", "Cantidad"])
visual_1_2 = VisualProcessor(frame_list=dataframe_list_3, features=["Ventas_USD"])


# p0 = PlotterStorage()

# # 2016-2021
# p0.add_graph(*BackendPlotter(processor=visual_1.set_content(y_label="Ventas [USD]", title_suffix="2016-2021").set_title("Ventas acumuladas en USD")).plot(), select_figures=True)
# p0.add_graph(*BackendPlotter(visual_1.set_content(y_label="Ventas Mensuales [Un.]", title_suffix="2016-2021").set_title("Cantidad de ventas mensuales")).plot_kind(kind="bar", resample="M"), select_figures=True)

# # 2019-2021
# p0.add_graph(*BackendPlotter(visual_1_1.set_content(y_label="Ventas [USD]", title_suffix="2019-2021").set_title("Ventas acumuladas en USD")).plot(), select_figures=True)
# p0.add_graph(*BackendPlotter(visual_1_2.set_content(y_label="Ventas Mensuales [USD]", title_suffix="2016-2021").set_title("Volumen de ventas semanales")).plot_kind(kind="bar", resample="W"), select_figures=True)


# descargar_objeto(p0, suffix="ventas totales")

In [16]:
# PLOT VENTAS
visual_2 = VisualProcessor(
    frame_list=d3.accumulated,
    features=features,
    y_label="Ventas [USD]",
    title_suffix="2016-2021",
)
visual_2_2 = VisualProcessor(
    frame_list=d4.accumulated,
    features=features,
    y_label="Ventas [USD]",
    title_suffix="2019-2021",
)

# PLOT_AREA
visual_3 = VisualProcessor(
    frame_list=d3.accumulated,
    features=features,
    y_label="Ventas acumuladas [USD]",
    title_suffix="2016-2021",
)
visual_3_2 = VisualProcessor(
    frame_list=d4.accumulated,
    features=features,
    y_label="Ventas acumuladas [USD]",
    title_suffix="2019-2021",
)

# BAR: Ventas mensuales y semanales
visual_4 = VisualProcessor(
    d3.datasets,
    features=features,
    y_label="Ventas mensuales [USD]",
    title_suffix="2016-2021",
)
visual_4_2 = VisualProcessor(
    d4.datasets,
    features=features,
    y_label="Ventas semanales [USD]",
    title_suffix="2019-2021",
)

# HIST:
visual_5 = VisualProcessor(
    d3.datasets,
    features=features,
    y_label="Ventas mensuales [USD]",
    title_suffix="2016-2021",
)
visual_5_2 = VisualProcessor(
    d4.datasets,
    features=features,
    y_label="Ventas semanales [USD]",
    title_suffix="2019-2021",
)

visuals = [
    visual_2,
    visual_2_2,
    visual_3,
    visual_3_2,
    visual_4,
    visual_4_2,
    visual_5,
    visual_5_2,
]

In [17]:
feature = "Empleado"

p1 = PlotterStorage()

# plot_and_storage(visuals, feature, p1, select_figures=True)

# descargar_objeto(p1, suffix=feature.lower())

In [18]:
import sys
sys.exit(0)

SystemExit: 0

In [ ]:
"""PLOTLY TEMPLATES:https://plotly.com/python/templates/

 ['ggplot2', 'seaborn', 'simple_white', 'plotly',
         'plotly_white', 'plotly_dark', 'presentation', 'xgridoff',
         'ygridoff', 'gridon', 'none']
"""


# VISUALIZACION: STACKED AREAS
# f = contenido.plot.area(title=f'VISUALIZACION: Ventas por {next(features_iter) (Apiladas)}', height=700, width=1200, labels={'value':'Ventas'}, template='plotly_dark')
# f.show()

"""
'add_barpolar', 'add_box', 'add_candlestick', 'add_carpet', 'add_choropleth', 'add_choroplethmapbox', 'add_cone', 'add_contour', 'add_contourcarpet', 'add_densitymapbox', 'add_funnel', 'add_funnelarea', 'add_heatmap', 'add_heatmapgl', 'add_histogram', 'add_histogram2d', 'add_histogram2dcontour', 'add_hline', 'add_hrect', 'add_icicle', 'add_image', 'add_indicator', 'add_isosurface', 'add_layout_image', 'add_mesh3d', 'add_ohlc', 'add_parcats', 'add_parcoords', 'add_pie', 'add_pointcloud', 'add_sankey', 'add_scatter', 'add_scatter3d', 'add_scattercarpet', 'add_scattergeo', 'add_scattergl', 'add_scattermapbox', 'add_scatterpolar', 'add_scatterpolargl', 'add_scattersmith', 'add_scatterternary', 'add_selection', 'add_shape', 'add_splom', 'add_streamtube', 'add_sunburst', 'add_surface', 'add_table', 'add_trace', 'add_traces', 'add_treemap', 'add_violin', 'add_vline', 'add_volume', 'add_vrect', 'add_waterfall', 'append_trace', 'batch_animate', 'batch_update', 'data', 'for_each_annotation', 'for_each_coloraxis', 'for_each_geo', 'for_each_layout_image', 'for_each_mapbox', 'for_each_polar', 'for_each_scene', 'for_each_selection', 'for_each_shape', 'for_each_smith', 'for_each_ternary', 'for_each_trace', 'for_each_xaxis', 'for_each_yaxis', 'frames', 'full_figure_for_development', 'get_subplot', 'layout', 'plotly_relayout', 'plotly_restyle', 'plotly_update', 'pop', 'print_grid', 'select_annotations', 'select_coloraxes', 'select_geos', 'select_layout_images', 'select_mapboxes', 'select_polars', 'select_scenes', 'select_selections', 'select_shapes', 'select_smiths', 'select_ternaries', 'select_traces', 'select_xaxes', 'select_yaxes', 'set_subplots', 'show', 'to_dict', 'to_html', 'to_image', 'to_json', 'to_ordered_dict', 'to_plotly_json', 'update', 'update_annotations', 'update_coloraxes', 'update_geos', 'update_layout', 'update_layout_images', 'update_mapboxes', 'update_polars', 'update_scenes', 'update_selections', 'update_shapes', 'update_smiths', 'update_ternaries', 'update_traces', 'update_xaxes', 'update_yaxes', 'write_html', 'write_image', 'write_json'
""";

In [ ]:
import sys

sys.exit(0)

SystemExit: 0

# (V) EXTRAS:

## 2do- PREPARAR DATASETS PARA MUESTREOS TEMPORALES

    2.1- Completar fechas faltante

    2.2- Armar muestreos temporales

    2.3- Visualizar poblacion


# ISOLAR EL COMPORTAMIENTO EN FRAGMENTOS, AJUSTANDO EL MARCO TEMPORAL SIN RESAMPLE



**EXPLICACION DEL GRAFICO**<br />
La variable "lista_mensual", es una lista cuyos elementos son datasets. <br />
Son 59 datasets que representan 1790 días en total<br />
Cada dataset representa un período de 30 días. <br />
Cada columna del gráfico representa el "len()" de un dataset. <br />
Algunos períodos tuvieron más cantidad de transacciones que otros. <br />

------DESC------

Primero tenemos que armar cada una de las series temporales

Para poder aplicar Cross-Validation a la serie temporal, es necesario completar con las fechas faltantes con algun valor default en sus variables. De esta forma podremos garantizar que nuestro folds representan el mismo timedelta.

------EJ------

Para hacer cross validation con scikit learn sobre data:

Si empezamos por 2016-01-09 y terminamos en 2020-12-02, tenemos 1790 días. Nuestro "log" es 1 día.

Como querémos cortes de igual tamaño, y sin gap al max_train_size y al test_size le damos el mismo valor.

Si quisieramos cortes bimensuales ingresamos los parámetros con valor 60 (días).

Para n_splits hacemos 1790 / 60 = 29.8 por eso elegimos 29 folds.

In [ ]:
from paquete_proyecto.data_prepare.muestreo import complete_dates, timeseries_cv

data_complete = complete_dates(data)

lista_mensual = timeseries_cv(data_complete, 59, 30, 30)


# VISUALIZACION:
# POBLACION: LONGITUD DE LOS DATASETS MUESTREADOS
longitud = []
for elemento in lista_mensual:
    longitud.append(len(elemento.dropna()))

pd.Series(longitud).plot.bar(figsize=(15, 5)).set(
    title="Cantidad de ventas cada 30 días"
)

<table>
    <tr>
        <td><iframe width="900" height="500" frameborder="0" scrolling="no" src="//plotly.com/~af.st22/7.embed"></iframe></td>
        <td><iframe width="900" height="500" frameborder="0" scrolling="no" src="//plotly.com/~af.st22/9.embed"></iframe></td>
    </tr>
</table>